<table style="width: 100%; border-style: none">
<tr style="border-style: none; background-color: #82a8cf">
<td style="border-style: none; width: 1%; text-align: left; font-size: 18px; color: #ffffff">Institut f&uuml;r Theoretische Physik<br /> <font color="#e6e6e6">Universit&auml;t zu K&ouml;ln </font></td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 18px; color: #ffffff">Prof. Dr. Simon Trebst<br /> <font color="#e6e6e6"> Christoph Berke </font> </td>
</tr>
</table>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h1 style="font-weight:200; text-align: center; margin: 0px; font-size: 48px; padding:0px; color: #606060">Statistische Physik </h1>
<h1 style="font-weight:light; text-align: center; margin: 10px; padding:0px; color: #606060">&Uuml;bungsblatt 3</h1>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h3 style="font-weight:400; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px; color: #606060">Wintersemester 23/24</h3>


<font size="4" color="#606060">**Website:** <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2023-StatPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2023-StatPhys.shtml</a></font>

<font size="4" color="#606060">**Abgabe**: <span style="color:#82a8cf"> 30.10.2023, 10:00 Uhr </span> <span style="float:right;">**Besprechung**: 31.10.2023 </span></font>

<font size="4" color="#606060">**Name**: <span style="color:#82a8cf"> Bitte geben Sie Ihren Namen an.  </span> </font>

<table style="border-style: none; width: 100%; background-color: #FFFFFF"><tr style="border-style: none;">
<td style="border-style: none; width:3%; text-align: left; font-size: 25px; font-weight: 200;background-color: #FFFFFF">Aufgabe 13: Simulation eines zweidimensionalen Gases, Teil 2 </td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 15px;background-color: #FFFFFF">[4 Punkte]</td></tr></table> 

Wie in der vergangenen Woche finden Sie nachfolgend alle Funktionen implementiert, die für die Simulation eines zweidimensionalen Gases unter Berücksichtigung von elastischen Kollisionen zwischen den Teilchen benötigt werden. Führen Sie die nachfolgenden Zellen aus und bearbeiten Sie anschließend die unten stehende, ausführliche Aufgabenstellung.

In [ ]:
using Random, LinearAlgebra, CairoMakie

In [ ]:
# Initialize positions and velocities of particles in a 2D box.
# x, y = Position arrays,
# vx, vy = velocity arrays,
# r = particle radius array
# v = particle velocity (abs. value)
# box = tuple with boundaries
function initialize_particles!(x, y, vx, vy, r, v, box)
    
    # extract boundaries
    xmin, xmax, ymin, ymax = box
    
    # initialize each particle individually
    for i in 1:length(x)
        
        # random position with distance r to boundary
        x[i] = xmin+2*r[i] + rand() * (xmax - xmin - 4*r[i])
        y[i] = ymin+2*r[i] + rand() * (ymax - ymin - 4*r[i])
        
        # random velocity direction
        angle = rand()*2*pi
        vx[i], vy[i] = cos(angle)*v, sin(angle)*v
        
    end
    
end

# Same as above, but take account of the finite dimension of each particle. 
function initialize_particles_without_overlap!(x, y, vx, vy, r, v, box)
    
    # extract boundaries
    xmin, xmax, ymin, ymax = box
    
    # initialize each particle individually
    for i in 1:length(x)
        
        # reset counter of maximal tries
        tries, maxtries = 0, 1000
        
        # random position with distance r to boundary and no overlap to other particles
        overlapping = true
        while overlapping
            x[i] = xmin+2*r[i] + rand()*(xmax - xmin - 4*r[i])
            y[i] = ymin+2*r[i] + rand()*(ymax - ymin - 4*r[i])
            overlapping = false
            for j in 1:i-1
                if (x[i]-x[j])^2 + (y[i]-y[j])^2 < 1.01*(r[i]+r[j])^2
                    overlapping = true
                end
            end
            tries += 1
            # maybe break loop because of maximum tries
            if tries > maxtries
                @error "Could not place particle! Exceeded $(max_tries) tries"
                return
            end
        end
        
       # random velocity direction
        angle = rand()*2*pi
        vx[i], vy[i] = cos(angle)*v, sin(angle)*v
        
    end
    
end

In [ ]:
function move_particles!(x, y, vx, vy, dt, r, box)
    
    # move all particles by dt
    x .+= vx .* dt
    y .+= vy .* dt
    
    # check collision with bounding box
    for i in 1:length(x)
        # left / right
        if x[i]-r[i] < box[1]
            vx[i] *= -1
        elseif x[i]+r[i] > box[2]
            vx[i] *= -1
        end
        # up / down
        if y[i]-r[i] < box[3]
            vy[i] *= -1
        elseif y[i]+r[i] > box[4]
            vy[i] *= -1
        end
    end
    return 0
end

In [ ]:
function collide_particles!(x, y, vx, vy, m, r)
    
    # check all particle pairs (i,j) for collision
    for i in 1:length(x)
        for j in 1:i-1
            # particles i and j are too close --> collision
            if (x[i]-x[j])^2 + (y[i]-y[j])^2 < (r[i]+r[j])^2
                er = [x[j]-x[i], y[j]-y[i]]
                er = er ./ norm(er)
                vi = er[1]*vx[i] + er[2]*vy[i]
                vj = er[1]*vx[j] + er[2]*vy[j]
                vip = 2*(m[i]*vi + m[j]*vj)/(m[i]+m[j])  -  vi
                vjp = 2*(m[i]*vi + m[j]*vj)/(m[i]+m[j])  -  vj
                vx[i] = vx[i] + (vip - vi)*er[1]
                vy[i] = vy[i] + (vip - vi)*er[2]
                vx[j] = vx[j] + (vjp - vj)*er[1]
                vy[j] = vy[j] + (vjp - vj)*er[2]
            end
            
        end
    end
    
end

### Vorbereitung: Aufenthaltswahrscheinlichkeit eines einzelnen Teilchens. ###
Wir betrachten jetzt die Aufenthaltswahrscheinlichkeit eines **einzelnen** Teilchens in der Box. Dazu unterteilen wir (in Gedanken) das Gesamtvolument in einen linken und rechten Teil mit den jeweiligen Volumina $p V$ und $(1-p) V$ (Achtung: $p$ ist nicht der Druck. Später wird klar, warum dieser Parameter trotzdem $p$ heißt). In der folgenden Zelle betrachten wir mehrere, jeweils fixierte Werte von $p$. Wir lassen die Simulation jeweils für eine gewisse Zeitspanne ```twait``` laufen, und messen anschließend, ob sich das Teilchen im linken oder rechten Teilvolumen befindet. Diese Messung wiederholen wir mehrfach (```Nmeasure``` mal). Anschließend stellen wir die Häufigkeiten, mit denen das Teilchen im linken Teilvolumen gemessen wird als Funktion der Volumengröße $p$ dar.

In [ ]:
### Parameter der Simulation ###
N = 10 # Anzahl der Teilchen
box = (0.0, 1, 0.0, 0.5) # Größe der Box
radius = 0.005 # Radius der Teilchen
v = 0.4 # Anfangsgeschwindigkeit

### Anfangsorte- und Geschwindigkeiten ###
x, y = zeros(N), zeros(N)
vx, vy  = zeros(N), zeros(N)
# Massen und Radien
m, r = ones(N), radius * ones(N)
initialize_particles_without_overlap!(x,y,vx,vy,r,v,box)

Nmeasure = 10_000 # Anzahl der Messungen
twait = 200       # Anzahl der Updateschritte zwischen den Messungen (groß für wirklich unabhängige Messungen)

ps = [0.1,0.3,0.5,0.7,0.9] # Unterschiedliche Werte für p
pleft = similar(ps) # Array um Anzahl der "Teilchen links"-Events zu speichern.

# Schleife über alle p
for i in eachindex(ps)
    left = 0 # Variable die Anzahl der Events "Teilchen links" zaehlt.
    # Schleife über alle Messungen
    for _ in 1:Nmeasure
        # Warte twait update Schritte zwischen zwei Messungen.
        for _ in 1:twait
            # Teilchen kollidieren.
            collide_particles!(x,y,vx,vy,m,r)
            # Teilchen fortbewegen.
            move_particles!(x,y,vx,vy,0.01,r,box)
        end
        
        # Messe am 1. Teilchen: Wenn im linken Teil mit Volumen ps[i]*box[2], erhöhe left
        (x[1] < ps[i] * box[2]) && (left += 1)
    end
    
    pleft[i] = left
end 


In [ ]:
# Darstellung der Haeufigkeiten als barplot.
fig, ax, p = barplot(ps, pleft)

# Plot verschönern
ax.xlabel = "p"
ax.ylabel = "# Teilchen links"
ax.yticks = 1000:2000:9000
ax.xticks = 0.1:0.2:0.9

fig

### Jetzt sind Sie gefragt: ###
Genau wie oben wird jetzt wiederholt der Ort eines Teilchens gemessen. Zwischen jeder Messung wird erneut eine gewisse Zeit abgewartet. Diesmal führen wir aber viele *Messreihen* durch (z.B. 4000 Reihen), wobei jede Reihe aus einer kleineren Anzahl an Einzelmessungen (z.B. 25 Messungen) besteht. Für jede einzelne Messreihe sollen sie abspeichern, wie oft das Teilchen im linken Teil der Box mit Volumen $pV$ gemessen wird.
Sie erhalten so 4000 Werte zwischen $k=0$ und $k=25$. Stellen Sie die Häufigkeiten der Werte von $k$ in einem Histogramm dar (mittels `hist`). Welcher Verteilung ähnelt das Histogramm? Stellen Sie diese Verteilung ebenfalls dar. 